# 1 Create OD Matrix

The goal of the following notebook is to compute an OD-matrix using the preprocessed Milan Dataset.

The cells denoted with the symbol \* may be skipped if you want to use the pre-computed OD matrix

___

To compute the OD-Matrix M we first divide the urban environment into squared tiles of a given side. Second,
we use real mobility data (the Milan Dataset) to estimate the flows between the tiles, thus obtaining an origin-destination matrix $M$ where an element $m_{o,d} \in M$ describes the number of vehicles’ trips that start in tile $o$
and end in tile $d$.
___

In [1]:
from utils import *
import geopandas as gpd
import pandas as pd
import sumolib
from skmob.tessellation import tilers
import json

import warnings
warnings.filterwarnings("ignore")

<module 'libsumo' from '/home/gcornacchia/anaconda3/envs/navigators/lib/python3.10/site-packages/libsumo/__init__.py'>


In [2]:
city = "milan_big"

#### File paths

In [3]:
# real mobility data path
mobility_data_path = f"../data/{city}/{city}_traj.csv"

# road network path
road_network_path = f"../data/{city}/{city}_road_network.net.xml"

# shapefile path
shapefile_path = f"../data/{city}/bbox_net_{city}.geojson"

# outputs directories
od_matrix_path = "../data"
dict_tile_edges_path =  "../data"

#### Load the real mobility data *

In [4]:
traj_D = pd.read_csv(mobility_data_path)
traj_D = skmob.TrajDataFrame(traj_D[['uid', 'datetime', 'lat', "lng"]], latitude='lat', longitude='lng', 
                                             user_id='uid', datetime='datetime')
traj_D[:4]

uid            datetime        lat       lng
0  193_0 2007-04-03 08:01:00  45.377006  9.277484
1  193_0 2007-04-03 08:01:55  45.391857  9.261229
2  193_0 2007-04-03 08:03:16  45.409712  9.262036
3  193_0 2007-04-03 08:05:52  45.415662  9.265230

In [5]:
len(traj_D['uid'].unique())

5617

#### Load the shapefile of the geographic area of interest

In [6]:
shape = gpd.GeoDataFrame.from_file(shapefile_path)

#### Create a squared tessellation of the city (size of 1km)

In [7]:
tile_size_meters = 1000
tessellation = tilers.tiler.get('squared', base_shape=shape, meters=tile_size_meters)

In [8]:
len(tessellation)

1044

In [9]:
from skmob.utils.plot import *
# style of the tessellation
tex_style = {'fillColor':'blue', 'color':'black', 'opacity': 0.2}

m = plot_gdf(shape, style_func_args=tex_style, zoom=12)
plot_gdf(tessellation, style_func_args=tex_style, zoom=12, map_f=m, popup_features=["tile_ID"])

#### Compute the OD matrix *

In [10]:
%%time
od_matrix = compute_od_matrix(traj_D, tessellation, traj_id="uid", self_loops=True)

CPU times: user 213 ms, sys: 19.3 ms, total: 233 ms
Wall time: 239 ms


In [11]:
od_matrix.sum()

5617.0

#### Save the OD matrix *

It will be used later to compute the Mobility Demand

In [12]:
with open(od_matrix_path+f'/{city}/{city}_od_matrix.npy', 'wb') as f:
    np.save(f, od_matrix)

In [13]:
with open(od_matrix_path+f'/{city}/{city}_od_matrix.npy', 'rb') as f:
    mb = np.load(f)

In [14]:
mb.sum()

5617.0

#### Load the road network

In [16]:
road_network = sumolib.net.readNet(road_network_path, withInternal=False)

In [17]:
print(len(road_network.getEdges()))
print(len(road_network.getNodes()))

46488
24063


#### Assign road network edges to the corresponding tile

In [18]:
dict_tile_edges = create_dict_tile_edges(road_network, tessellation, exclude_roundabouts=True)

In [19]:
len(dict_tile_edges.keys())

727

In [20]:
tile_2_keep = list(dict_tile_edges.keys())

In [21]:
tex_od = tessellation[tessellation["tile_ID"].isin(tile_2_keep)]

In [22]:
from skmob.utils.plot import *
# style of the tessellation
tex_style = {'fillColor':'blue', 'color':'black', 'opacity': 0.2}

#m = plot_gdf(shape, style_func_args=tex_style, zoom=12)
plot_gdf(tex_od, style_func_args=tex_style, zoom=12, map_f=None, popup_features=["tile_ID"])

In [23]:
output_file = open(dict_tile_edges_path+f"/{city}/dict_tile_edges.json", "w")
json.dump(dict_tile_edges, output_file)
output_file.close()

In [24]:
f = open(dict_tile_edges_path+f"/{city}/dict_tile_edges.json")
d = json.load(f)